In [60]:
# Add relevant modules
import pandas as pd
import numpy as np
import os
from scipy import signal
from scipy.io import wavfile
import math
import sys
import pyaudio
import wave
import librosa
import soundfile as sf

In [61]:
#loads the file and its sampling frequency
fs, data = wavfile.read('Recordings/Test.wav')
#open a wav format music  
f = wave.open("Recordings/Test.wav","rb")  
#instantiate PyAudio  
p = pyaudio.PyAudio()  

chunk = 1024

In [62]:
#open stream  
stream = p.open(format = p.get_format_from_width(f.getsampwidth()),  
                channels = f.getnchannels(),  
                rate = f.getframerate(),  
                output = True)  
#read data  
data = f.readframes(chunk)  

In [63]:
#play stream  
while data:  
    stream.write(data)  
    data = f.readframes(chunk)  

KeyboardInterrupt: 

In [ ]:
#stop stream  
stream.stop_stream()  
stream.close()  

In [ ]:
#close PyAudio  
p.terminate() 

In [ ]:
#adjust framerate and convert stereo to mono and output new file
data1, sample_rate = librosa.load( 'Recordings/Test.wav', sr=16000, mono=True )
wavfile.write('Downsampled.wav', sample_rate, data1)

In [ ]:
#load new downsampled wav
fs2, data2 = wavfile.read('Downsampled.wav')

#get the duration of the new wav
duration = len(data2)/fs2

#negative file length for wav file segmentation
negative_file_length = -len(data2)

#decide chunk length
chunk_length = 200

#determine how many wav files will be made
num_of_files = len(data2)//chunk_length

#list of time segments
arr = []

#Add each of the segments into the list
for i in range(num_of_files):
    arr.append(data2 [ i * chunk_length : negative_file_length + chunk_length + ( i * chunk_length)])
    #conversion to numpy array
arr = np.array(arr)

In [ ]:
bandpass_array = []

# Define bandpass parameters
num_filters = 120
order = 3
sample_rate = fs2
centre_freq = 100
band_width = 100
spacing = 50

# Create an array of bandpass filters
for i in range (num_filters):
    # Equally space upper and lower bounds around the centre frequency
    lower_freq = (centre_freq + spacing * i) - band_width / 2
    upper_freq = (centre_freq + spacing * i) + band_width / 2

    # Create the bandpass filter
    sos = signal.butter(order,[lower_freq, upper_freq], btype='bandpass', output='sos', fs = sample_rate)
    
    # Add the bandpass filter to the array
    bandpass_array.append(sos)

In [ ]:
filtered_chunks = []

# Apply bank of bandpass filters to each chunk
for chunk in arr:
    for bandpass_filter in (bandpass_array):
        filtered_chunk = signal.sosfilt(bandpass_filter, chunk)
        filtered_chunks.append(filtered_chunk)
filtered_chunks


[array([-5.45753719e-16, -3.12549180e-15, -9.16218457e-15, -1.98028228e-14,
        -3.71510727e-14, -6.42708000e-14, -1.03879076e-13, -1.57384766e-13,
        -2.25146924e-13, -3.07394931e-13, -4.04876480e-13, -5.19137596e-13,
        -6.52218415e-13, -8.06134157e-13, -9.82927889e-13, -1.18375514e-12,
        -1.40734762e-12, -1.65155964e-12, -1.91481355e-12, -2.19387400e-12,
        -2.48297574e-12, -2.77591011e-12, -3.06734332e-12, -3.35258428e-12,
        -3.62770054e-12, -3.89012055e-12, -4.13774693e-12, -4.36758357e-12,
        -4.57660780e-12, -4.76287955e-12, -4.92420961e-12, -5.05730322e-12,
        -5.15936876e-12, -5.22879709e-12, -5.26379772e-12, -5.26208533e-12,
        -5.22145801e-12, -5.13932343e-12, -5.01449563e-12, -4.84928930e-12,
        -4.64624343e-12, -4.40696166e-12, -4.13436100e-12, -3.83113241e-12,
        -3.49906746e-12, -3.14048971e-12, -2.75809143e-12, -2.35406185e-12,
        -1.92792106e-12, -1.47681656e-12, -9.99524679e-13, -4.96948361e-13,
         2.9

In [ ]:
#get rms values for filtered chunks
rms_values = []

for filtered_chunk in filtered_chunks:
    rms = np.sqrt(np.mean(filtered_chunk**2))
    rms_values.append(rms)
    
filtered_chunks

[array([-5.45753719e-16, -3.12549180e-15, -9.16218457e-15, -1.98028228e-14,
        -3.71510727e-14, -6.42708000e-14, -1.03879076e-13, -1.57384766e-13,
        -2.25146924e-13, -3.07394931e-13, -4.04876480e-13, -5.19137596e-13,
        -6.52218415e-13, -8.06134157e-13, -9.82927889e-13, -1.18375514e-12,
        -1.40734762e-12, -1.65155964e-12, -1.91481355e-12, -2.19387400e-12,
        -2.48297574e-12, -2.77591011e-12, -3.06734332e-12, -3.35258428e-12,
        -3.62770054e-12, -3.89012055e-12, -4.13774693e-12, -4.36758357e-12,
        -4.57660780e-12, -4.76287955e-12, -4.92420961e-12, -5.05730322e-12,
        -5.15936876e-12, -5.22879709e-12, -5.26379772e-12, -5.26208533e-12,
        -5.22145801e-12, -5.13932343e-12, -5.01449563e-12, -4.84928930e-12,
        -4.64624343e-12, -4.40696166e-12, -4.13436100e-12, -3.83113241e-12,
        -3.49906746e-12, -3.14048971e-12, -2.75809143e-12, -2.35406185e-12,
        -1.92792106e-12, -1.47681656e-12, -9.99524679e-13, -4.96948361e-13,
         2.9

In [ ]:
#sin wave values
sin_values = []

for i in range(num_of_files):
    chunk_time = i * duration / num_of_files
    time = np.arange(chunk_time, chunk_time+chunk_length)
    time_seconds = time / 16000
    sin_wave = np.sin(2 * np.pi * centre_freq * i * time_seconds)
    varying_amplitude = rms * sin_wave
    for val in sin_wave.tolist():
        sin_values.append(val)
        
sin_values

[0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0

In [69]:
#synthesize chunks
synthesized_chunk = varying_amplitude

In [67]:
#output a wav file
concatenated_chunks = np.concatenate(sin_values)

with wave.open("output.wav", 'w') as output_file:
        output_file.setparams((1, 2, 16000, len(concatenated_chunks), "NONE", "Uncompressed"))
        output_file.writeframes(concatenated_chunks.astype(np.int16).tobytes())

ValueError: zero-dimensional arrays cannot be concatenated